# Modelagem de Risco de Crédito

O objetivo deste projeto é avaliar o risco de crédito de clientes e prever se eles vão pagar ou não, utilizando dados financeiros e demográficos considerando que eles já solicitarem crédito. Será utilizado uma abordagem utilizando o framework CRISP-DM, e neste arquivo será dado ínicio aplicando técnicas de análise exploratória de dados. O projeto será organizado da seguinte forma:

- EDA 
- Feature Enginnering
- Pré-processamento
- Modelagem
- Deploy

# Dicionário de Dados – Credit Risk Dataset

| **Nome da Variável**              | **Descrição**                                           | **Tipo de Dado**         | **Exemplo de Valor**       | **Observações** |
|----------------------------------|----------------------------------------------------------|---------------------------|----------------------------|-----------------|
| **person_age**                   | Idade do indivíduo.                                    | Numérico (inteiro)       | 35                         | Representa a idade do solicitante do empréstimo. |
| **person_income**                | Renda anual do indivíduo.                              | Numérico (contínuo)      | 60000                      | Normalmente expressa em dólares por ano. |
| **person_home_ownership**        | Tipo de posse da residência.                           | Categórico               | "OWN", "RENT", "MORTGAGE"  | Indica se o indivíduo possui, aluga ou está financiando o imóvel. |
| **person_emp_length**            | Tempo de emprego (em anos).                            | Numérico (inteiro)       | 5                          | Número de anos que o indivíduo está empregado. |
| **loan_intent**                  | Finalidade do empréstimo.                              | Categórico               | "EDUCATION", "MEDICAL", "PERSONAL", "VENTURE", "HOMEIMPROVEMENT", "DEBTCONSOLIDATION" | Indica o propósito declarado do empréstimo. |
| **loan_grade**                   | Grau de risco do empréstimo.                           | Categórico ordinal       | "A", "B", "C", "D", "E", "F", "G" | Classificação de risco atribuída ao empréstimo. |
| **loan_amnt**                    | Valor total do empréstimo solicitado.                  | Numérico (contínuo)      | 10000                      | Montante total do empréstimo em dólares. |
| **loan_int_rate**                | Taxa de juros do empréstimo (em %).                    | Numérico (contínuo)      | 11.5                       | Percentual de juros aplicado ao empréstimo. |
| **loan_status**                  | Situação do empréstimo (inadimplência ou não).          | Binário (0/1)            | 0 ou 1                     | 0 = Não inadimplente, 1 = Inadimplente. |
| **loan_percent_income**          | Percentual da renda comprometida com o empréstimo.      | Numérico (contínuo)      | 0.25                       | Calculado como valor do empréstimo dividido pela renda anual. |
| **cb_person_default_on_file**    | Histórico de inadimplência anterior.                   | Categórico binário       | "Y", "N"                   | Indica se o indivíduo já teve inadimplência anterior (Y = Sim, N = Não). |
| **cb_preson_cred_hist_length**   | Tempo de histórico de crédito (em anos).               | Numérico (inteiro)       | 10                         | Representa há quanto tempo o indivíduo possui histórico de crédito. |


In [16]:
import sys
import os

# Caminho da raiz do projeto
ROOT_DIR = os.path.abspath(os.path.join(os.getcwd(), ".."))
if ROOT_DIR not in sys.path:
    sys.path.append(ROOT_DIR)

print("ROOT_DIR:", ROOT_DIR)

ROOT_DIR: c:\Users\eduar\OneDrive\Documentos\SandBox\Projetos\risco_ml


In [17]:
from src.utils.paths import data_path

In [47]:
# Pacotes de análise e manipulação de dados
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# desenvolver gráficos e dashs
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns

import statsmodels.api as sm
import scipy.stats as stats
from sklearn.preprocessing import LabelEncoder
import warnings
warnings.filterwarnings("ignore")

In [48]:
credit_risk_dict = {
    "person_age": "Idade do indivíduo (anos)",
    "person_income": "Renda anual do indivíduo",
    "person_home_ownership": "Tipo de posse da residência",
    "person_emp_length": "Tempo de emprego (em anos)",
    "loan_intent": "Finalidade do empréstimo",
    "loan_grade": "Grau de risco do empréstimo",
    "loan_amnt": "Valor total do empréstimo solicitado",
    "loan_int_rate": "Taxa de juros do empréstimo (%)",
    "loan_status": "Situação do empréstimo (inadimplente ou não)",
    "loan_percent_income": "Percentual da renda comprometida com o empréstimo",
    "cb_person_default_on_file": "Histórico de inadimplência anterior",
    "cb_preson_cred_hist_length": "Tempo de histórico de crédito (em anos)"
}

In [20]:
csv_file = data_path("credit_risk_dataset.csv")
dados = pd.read_csv(csv_file, sep=",")

In [21]:
dados.head()

person_age  person_income person_home_ownership  person_emp_length  \
0          22          59000                  RENT              123.0   
1          21           9600                   OWN                5.0   
2          25           9600              MORTGAGE                1.0   
3          23          65500                  RENT                4.0   
4          24          54400                  RENT                8.0   

  loan_intent loan_grade  loan_amnt  loan_int_rate  loan_status  \
0    PERSONAL          D      35000          16.02            1   
1   EDUCATION          B       1000          11.14            0   
2     MEDICAL          C       5500          12.87            1   
3     MEDICAL          C      35000          15.23            1   
4     MEDICAL          C      35000          14.27            1   

   loan_percent_income cb_person_default_on_file  cb_person_cred_hist_length  
0                 0.59                         Y                           3  
1                 0.10                         N                           2  
2                 0.57                         N                           3  
3                 0.53                         N                           2  
4                 0.55                         Y                           4

In [22]:
dados.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32581 entries, 0 to 32580
Data columns (total 12 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   person_age                  32581 non-null  int64  
 1   person_income               32581 non-null  int64  
 2   person_home_ownership       32581 non-null  object 
 3   person_emp_length           31686 non-null  float64
 4   loan_intent                 32581 non-null  object 
 5   loan_grade                  32581 non-null  object 
 6   loan_amnt                   32581 non-null  int64  
 7   loan_int_rate               29465 non-null  float64
 8   loan_status                 32581 non-null  int64  
 9   loan_percent_income         32581 non-null  float64
 10  cb_person_default_on_file   32581 non-null  object 
 11  cb_person_cred_hist_length  32581 non-null  int64  
dtypes: float64(3), int64(5), object(4)
memory usage: 3.0+ MB


In [23]:
# Taxa de nulos
taxa_nulos = dados.isnull().sum()/len(dados)*100
taxa_nulos

person_age                    0.000000
person_income                 0.000000
person_home_ownership         0.000000
person_emp_length             2.747000
loan_intent                   0.000000
loan_grade                    0.000000
loan_amnt                     0.000000
loan_int_rate                 9.563856
loan_status                   0.000000
loan_percent_income           0.000000
cb_person_default_on_file     0.000000
cb_person_cred_hist_length    0.000000
dtype: float64

In [24]:
credit_risk_dict

{'person_age': 'Idade do indivíduo (anos)',
 'person_income': 'Renda anual do indivíduo',
 'person_home_ownership': 'Tipo de posse da residência',
 'person_emp_length': 'Tempo de emprego (em anos)',
 'loan_intent': 'Finalidade do empréstimo',
 'loan_grade': 'Grau de risco do empréstimo',
 'loan_amnt': 'Valor total do empréstimo solicitado',
 'loan_int_rate': 'Taxa de juros do empréstimo (%)',
 'loan_status': 'Situação do empréstimo (inadimplente ou não)',
 'loan_percent_income': 'Percentual da renda comprometida com o empréstimo',
 'cb_person_default_on_file': 'Histórico de inadimplência anterior',
 'cb_preson_cred_hist_length': 'Tempo de histórico de crédito (em anos)'}

Como a quantidade de nulos é pequena, pode-se considerar a opção de apagar esses registros mais para frente.

In [25]:
dados.describe()

person_age  person_income  person_emp_length     loan_amnt  \
count  32581.000000   3.258100e+04       31686.000000  32581.000000   
mean      27.734600   6.607485e+04           4.789686   9589.371106   
std        6.348078   6.198312e+04           4.142630   6322.086646   
min       20.000000   4.000000e+03           0.000000    500.000000   
25%       23.000000   3.850000e+04           2.000000   5000.000000   
50%       26.000000   5.500000e+04           4.000000   8000.000000   
75%       30.000000   7.920000e+04           7.000000  12200.000000   
max      144.000000   6.000000e+06         123.000000  35000.000000   

       loan_int_rate   loan_status  loan_percent_income  \
count   29465.000000  32581.000000         32581.000000   
mean       11.011695      0.218164             0.170203   
std         3.240459      0.413006             0.106782   
min         5.420000      0.000000             0.000000   
25%         7.900000      0.000000             0.090000   
50%        10.990000      0.000000             0.150000   
75%        13.470000      0.000000             0.230000   
max        23.220000      1.000000             0.830000   

       cb_person_cred_hist_length  
count                32581.000000  
mean                     5.804211  
std                      4.055001  
min                      2.000000  
25%                      3.000000  
50%                      4.000000  
75%                      8.000000  
max                     30.000000

**Análise**

- Existe um valor discrepante na variável idade onde a mesma tem um valor de 144 anos, o que implica em um tempo de emprego inexistente de 123 anos de trabalho. Nesse sentido, foi feito um filtro onde consideramos idades menor ou igual a 110 anos

In [26]:
dados = dados[dados['person_age'] <= 110]
dados = dados[dados['person_emp_length'] <= 110]

In [27]:
dados['loan_status'].value_counts()

loan_status
0    24854
1     6825
Name: count, dtype: int64

**Análise**

Podemos identificar que existe um desbalanceamento de classe entre as populações adimplentes e inadimplentes. Nesse projeto, estaremos com o foco de classificar potenciais clientes a oferecerem perdas ao banco, ou seja, inadimplentes, então, nesse caso, nossa classe minoritária será o target 1 onde possuem bem menos dados.

In [28]:
numericas = dados.select_dtypes(include=['int64', 'float64'])

correlacao = numericas.corr().round(2)
fig = px.imshow(
    correlacao,
    text_auto=True,
    color_continuous_scale='RdBu_r',
    origin='upper',
    labels=dict(x="Variáveis", y="Variáveis", color="Correlação"),
    width=1000,
    height=1000
)

fig.update_xaxes(side="top", tickfont=dict(size=12))
fig.update_yaxes(tickfont=dict(size=12))
fig.update_traces(textfont_size=14)

fig.show()

**Análise**

O tempo de histórico de crédito está fortemente correlacionada com a variável idade, cerca de 0.86 indicando que as duas podem ter alguma relação linear.

### Existe alguma relação entre grau de risco e o valor solicitado do empréstimo?

In [29]:
dados.head()

person_age  person_income person_home_ownership  person_emp_length  \
1          21           9600                   OWN                5.0   
2          25           9600              MORTGAGE                1.0   
3          23          65500                  RENT                4.0   
4          24          54400                  RENT                8.0   
5          21           9900                   OWN                2.0   

  loan_intent loan_grade  loan_amnt  loan_int_rate  loan_status  \
1   EDUCATION          B       1000          11.14            0   
2     MEDICAL          C       5500          12.87            1   
3     MEDICAL          C      35000          15.23            1   
4     MEDICAL          C      35000          14.27            1   
5     VENTURE          A       2500           7.14            1   

   loan_percent_income cb_person_default_on_file  cb_person_cred_hist_length  
1                 0.10                         N                           2  
2                 0.57                         N                           3  
3                 0.53                         N                           2  
4                 0.55                         Y                           4  
5                 0.25                         N                           2

In [30]:
fig = px.box(
    dados,
    x="loan_grade",
    y="loan_amnt",
    color="loan_grade",
    title="Relação entre Grau de Risco e Valor Solicitado do Empréstimo",
    labels={
        "loan_grade": "Grau de Risco do Empréstimo",
        "loan_amnt": "Valor Solicitado (USD)"
    },
    points="all",
    category_orders={"loan_grade": ["A", "B", "C", "D", "E", "F", "G"]}
)

fig.update_layout(
    template="plotly_white",
    title_font_size=18,
    xaxis_title_font_size=14,
    yaxis_title_font_size=14
)

fig.show()

**Análise**

Existe uma relação moderada entre o grau de risco e o valor solicitado, empréstimos de maior risco estão associados a valores médios mais altos e maior variabilidade, enquanto os de menor risco concentram-se em valores mais baixos e estáveis.

### A taxa de juros de empréstimo é menor para pessoas que possuem um tempo empregado elevado?

In [31]:
fig = px.scatter(
    dados,
    x="person_emp_length",
    y="loan_int_rate",
    trendline="ols",
    title="Relação entre Tempo de Emprego e Taxa de Juros do Empréstimo",
    labels={
        "person_emp_length": "Tempo de Emprego (anos)",
        "loan_int_rate": "Taxa de Juros (%)"
    },
    opacity=0.6
)

fig.update_layout(
    template="plotly_white",
    title_font_size=18,
    xaxis_title_font_size=14,
    yaxis_title_font_size=14
)

fig.show()

In [32]:
corr = dados['person_emp_length'].corr(dados['loan_int_rate'])
print(f"Correlação entre tempo de emprego e taxa de juros: {corr:.3f}")

Correlação entre tempo de emprego e taxa de juros: -0.058


**Análise**

Graficamente percebe-se uma leve uma curva na relação entre taxa de juros e tempo de emprego, onde mostra que a taxa de juros cai levemente quando o tempo de emprego aumenta. Além disso, possui uma correlação negativa fraca, o que demonstra ser apenas uma baixa relação entre essas variáveis.

### Qual a média dos valores solicitados com base no motivo do emprestimo?

In [33]:
media_valor_por_finalidade = (
    dados
    .groupby('loan_intent')['loan_amnt']
    .mean()
    .reset_index()
    .sort_values(by='loan_amnt', ascending=False)
)

# Criando o gráfico
fig = px.bar(
    media_valor_por_finalidade,
    x='loan_intent',
    y='loan_amnt',
    text='loan_amnt',
    color='loan_amnt',
    color_continuous_scale='Blues',
    title='Valor médio de empréstimo solicitado por finalidade',
)

# Ajustes de layout
fig.update_traces(
    texttemplate='R$ %{text:,.2f}',
    textposition='outside'
)

fig.update_layout(
    xaxis_title='Finalidade do Empréstimo',
    yaxis_title='Valor Médio Solicitado (R$)',
    title_font=dict(size=18, family='Arial', color='black'),
    xaxis_tickangle=-30,
    plot_bgcolor='white',
    showlegend=False,
    coloraxis_showscale=False
)

fig.show()

In [34]:
dados['loan_intent'].value_counts()

loan_intent
EDUCATION            6288
MEDICAL              5897
VENTURE              5553
PERSONAL             5367
DEBTCONSOLIDATION    5064
HOMEIMPROVEMENT      3510
Name: count, dtype: int64

### Dentre as categorias que ficaram abaixo da finalidade de emprestimo residencial, existe diferença significativa na média do valor solicitado entre os diferentes tipos de empréstimo?

Para responder essa pergunta, devemos aplicar conceitos estatísticos mais robustos. A técnica utilizada será **ANOVA** 

Ela é uma técnica estatística usada para comparar médias de dois ou mais grupos e verificar se há diferenças significativas entre elas. Ela funciona da seguinte forna:

- Olhar para a variação entre os grupos e comparar com a variação dentro dos grupos. Se a variação entre os grupos for muito maior que a variação dentro dos grupos, isso sugere que as médias são diferentes.

In [35]:
education = dados[dados['loan_intent'] == 'EDUCATION']['loan_amnt']
medical = dados[dados['loan_intent'] == 'MEDICAL']['loan_amnt']
venture = dados[dados['loan_intent'] == 'VENTURE']['loan_amnt']
personal = dados[dados['loan_intent'] == 'PERSONAL']['loan_amnt']
debt = dados[dados['loan_intent'] == 'DEBTCONSOLIDATION']['loan_amnt']

# ANOVA unidirecional
f_stat, p_value = stats.f_oneway(education, medical, venture, personal, debt)

print("F-statistic:", f_stat)
print("p-value:", p_value)

if p_value < 0.05:
    print("A diferença entre as médias é estatisticamente significativa.")
else:
    print("Não há diferença estatisticamente significativa entre as médias.")

F-statistic: 2.613298810241591
p-value: 0.033469880068211784
A diferença entre as médias é estatisticamente significativa.


**Análise**

Por mais que tenha-se mais registros de solicitação de créditos no motivo educacional, a média do valor solicitado pelo objetivo do empréstimo com maior financeiro foi residencial. Além disso, para as outras finalidades existe uma diferença significativa na média entre elas

### Qual tipo de finalidade de empréstimo é mais solicitada e qual é a taxa de inadimplência?

In [36]:
quantidade = dados.groupby('loan_intent').size().reset_index(name='Quantidade')

inadimplencia = dados.groupby('loan_intent')['loan_status'].mean().reset_index(name='Taxa_Inadimplencia')
inadimplencia['Taxa_Inadimplencia'] = inadimplencia['Taxa_Inadimplencia'] * 100  # converter para %

resumo = quantidade.merge(inadimplencia, on='loan_intent')
resumo = resumo.sort_values(by='Quantidade', ascending=False)

fig = go.Figure()

# Barras: quantidade de empréstimos
fig.add_trace(go.Bar(
    x=resumo['loan_intent'],
    y=resumo['Quantidade'],
    name='Quantidade de Empréstimos',
    marker_color='#0B3C5D',
    text=resumo['Quantidade'],
    textposition='auto'
))

# Linha: taxa de inadimplência
fig.add_trace(go.Scatter(
    x=resumo['loan_intent'],
    y=resumo['Taxa_Inadimplencia'],
    name='Taxa de Inadimplência (%)',
    yaxis='y2',
    mode='lines+markers',
    marker=dict(color='#D9534F', size=8)
))

# Layout
fig.update_layout(
    title='Solicitações de Empréstimos x Taxa de Inadimplência por Finalidade',
    xaxis_title='Finalidade do Empréstimo',
    yaxis=dict(
        title='Quantidade de Empréstimos',
        side='left'
    ),
    yaxis2=dict(
        title='Taxa de Inadimplência (%)',
        overlaying='y',
        side='right'
    ),
    legend=dict(x=0.8, y=1.1),
    bargap=0.3
)

fig.show()

In [37]:
resumo

loan_intent  Quantidade  Taxa_Inadimplencia
1          EDUCATION        6288           16.952926
3            MEDICAL        5897           26.538918
5            VENTURE        5553           14.658743
4           PERSONAL        5367           19.489473
0  DEBTCONSOLIDATION        5064           28.376777
2    HOMEIMPROVEMENT        3510           25.555556

**Análise**

- Educação
A solicitação de empréstimo para fins educionais possuem um alto valor de registros, entretanto, a taxa de inadimplência desse requisito é a segunda menor. Isso pode ser pelo fato de que o indivíduo consegue alcançar melhores salários no mercado e uma maior probabilidade de quitação da dívida.

- Consolidação de dívidas
Esse tipo de solicitação é quando junta várias dívidas em uma só. Dado o montante final do valor a pagar, na maioria das vezes a pessoa que solicitou não consegue quitar a dívida por conta do aumento de juros. O que leva a uma taxa de inadimplência mais alta.

### Qual a faixa etária de cada uma dessas solicitações?

In [38]:
bins = [20, 30, 40, 50, 60, 65, 95]
labels = ['20-29', '30-39', '40-49', '50-59', '60-64', '65+']

dados['faixa_etaria'] = pd.cut(dados['person_age'], bins=bins, labels=labels, right=False)
dados.head()

person_age  person_income person_home_ownership  person_emp_length  \
1          21           9600                   OWN                5.0   
2          25           9600              MORTGAGE                1.0   
3          23          65500                  RENT                4.0   
4          24          54400                  RENT                8.0   
5          21           9900                   OWN                2.0   

  loan_intent loan_grade  loan_amnt  loan_int_rate  loan_status  \
1   EDUCATION          B       1000          11.14            0   
2     MEDICAL          C       5500          12.87            1   
3     MEDICAL          C      35000          15.23            1   
4     MEDICAL          C      35000          14.27            1   
5     VENTURE          A       2500           7.14            1   

   loan_percent_income cb_person_default_on_file  cb_person_cred_hist_length  \
1                 0.10                         N                           2   
2                 0.57                         N                           3   
3                 0.53                         N                           2   
4                 0.55                         Y                           4   
5                 0.25                         N                           2   

  faixa_etaria  
1        20-29  
2        20-29  
3        20-29  
4        20-29  
5        20-29

In [39]:
faixa_por_finalidade = pd.crosstab(dados['loan_intent'], dados['faixa_etaria'])

fig = px.imshow(
    faixa_por_finalidade,
    text_auto=True, 
    labels=dict(x="Faixa Etária", y="Finalidade do Empréstimo", color="Quantidade"),
    x=faixa_por_finalidade.columns,
    y=faixa_por_finalidade.index,
    aspect="auto",
    color_continuous_scale='Blues'
)

fig.update_layout(
    title='Contagem de Empréstimos por Faixa Etária e Finalidade'
)

fig.show()

**Análise**

Podemos ver que a solicitação de empréstimos envolvendo a edução é mais numerosa no público mais jovem, entre 20-29 anos. Além disso, o mesmo público também é o que mais solicita empréstimo.

### Qual a relação entre Renda anual do indivíduo e valor total do empréstimo solicitado?

In [40]:
fig = px.scatter(
    dados,
    x='person_income',
    y='loan_amnt',
    title='Relação entre Renda Anual e Valor do Empréstimo (LOG)',
    labels={'person_income':'Renda Anual (R$)', 'loan_amnt':'Valor do Empréstimo (R$)'},
    trendline='ols',
    opacity=0.6
)

fig.update_xaxes(type='log', title='Renda Anual (R$) - log')
fig.update_yaxes(type='log', title='Valor do Empréstimo (R$) - log')

fig.show()

In [41]:
correlacao = dados['person_income'].corr(dados['loan_amnt'])
print(f"Correlação entre renda e valor do empréstimo: {correlacao:.2f}")

Correlação entre renda e valor do empréstimo: 0.31


**Análise**

Existe uma correlação positiva fraca entre a renda anual e o valor do empréstimo solicitado. Em geral, indivíduos com renda maior tendem a solicitar empréstimos maiores, mas a relação não é muito forte.

### Quanto maior a taxa de juros, maior a taxa de inadimplência?

In [42]:
fig = px.box(
    dados,
    x="loan_status",
    y="loan_int_rate",
    color="loan_status",
    labels={"loan_status": "Situação do Empréstimo", "loan_int_rate": "Taxa de Juros (%)"},
    title="Distribuição da Taxa de Juros por Situação do Empréstimo"
)

fig.update_layout(title_x=0.5)
fig.show()

In [43]:
media_juros = (
    dados.groupby('loan_status')['loan_int_rate']
    .mean()
    .reset_index()
    .rename(columns={'loan_int_rate': 'media_juros'})
)

juros_adimplente = media_juros.loc[media_juros['loan_status'] == 0, 'media_juros'].values[0]
juros_inadimplente = media_juros.loc[media_juros['loan_status'] == 1, 'media_juros'].values[0]

diferenca_percentual = ((juros_inadimplente - juros_adimplente) / juros_adimplente) * 100
print(f"A taxa média de juros dos inadimplentes é {diferenca_percentual:.2f}% maior que a dos adimplentes.")

A taxa média de juros dos inadimplentes é 25.42% maior que a dos adimplentes.


**Análise**

A taxa de juros é menor para quem é um bom pagador, e é maior para quem é um mau pagador.

### Pessoas com histórico de inadimplência tem maior probabilidade de ficarem inadimplentes novamente?

In [44]:
taxa_inadimplencia = (
    dados.groupby('cb_person_default_on_file')['loan_status']
    .mean()
    .reset_index()
    .rename(columns={'loan_status': 'taxa_inadimplencia'})
)

taxa_inadimplencia

cb_person_default_on_file  taxa_inadimplencia
0                         N            0.180838
1                         Y            0.375622

Pessoas sem histórico tem uma taxa de 18% de serem inadimplentes e pessoas com histórico tem 37% de chance.

In [45]:
taxa_sem_hist = taxa_inadimplencia.loc[taxa_inadimplencia['cb_person_default_on_file'] == 'N', 'taxa_inadimplencia'].values[0]
taxa_com_hist = taxa_inadimplencia.loc[taxa_inadimplencia['cb_person_default_on_file'] == 'Y', 'taxa_inadimplencia'].values[0]

diferenca_percentual = ((taxa_com_hist - taxa_sem_hist) / taxa_sem_hist) * 100

print(f"A taxa de inadimplência é {diferenca_percentual:.2f}% maior entre quem já teve histórico de inadimplência.")

A taxa de inadimplência é 107.71% maior entre quem já teve histórico de inadimplência.


In [46]:
fig = px.bar(
    taxa_inadimplencia,
    x='cb_person_default_on_file',
    y='taxa_inadimplencia',
    color='cb_person_default_on_file',
    text=taxa_inadimplencia['taxa_inadimplencia'].apply(lambda x: f"{x*100:.1f}%"),
    title=f"Taxa de Inadimplência por Histórico de Pagamento<br><sup>Diferença: {diferenca_percentual:.2f}%</sup>",
    labels={
        'cb_person_default_on_file': 'Histórico de Inadimplência (Y = Sim, N = Não)',
        'taxa_inadimplencia': 'Taxa de Inadimplência'
    }
)

fig.update_traces(textposition='outside')
fig.update_layout(title_x=0.5)
fig.show()

### Conclusão

- Pessoas mais jovens tendem a solicitar mais empréstimos na finalidade de educação, pois, estão tentando melhorar de vida atráves dos memos. Além disso, possuem a menor taxa de inadimplência dado o conjunto de dados atual, nos dando a dizer que com um aumento de salário melhor atráves de inventimentos educacionais, tendem a quitar a dívida.

- Retornando ao perfil com idade mais juvenil, eles também são os que mais solicitam empréstimo, dado que estão começando a vida agora e estão tentando estruturar a vida pessoal deles.

- Pessoas que são mau pagadoras tem em média um juros de 25.42% maior que o dos adimplentes.

- Quanto maior a renda, maior o valor solicitado do empréstimo, dado que, as dívidas criadas quando se recebe um maior salário, são dívidas mais altas.

- Quem já foi inadimplente tem uma taxa de inadimplência 107% maior do que quem nunca foi.